# Data analysis

Here we will try some analysis on the data we have collected. We will try to find out the following things:

- Spatial Regression Analysis: 
We can perform spatial regression analysis to understand the relationships between tree distribution, ecological benefits, and environmental factors. This can help identify areas where planting specific tree species can have the most significant impact on reducing pollution or increasing oxygen levels.

Model documentation examples: 
- https://deepforest.readthedocs.io/en/latest/getting_started.html#sample-data
- https://github.com/kodujdlapolski/tree-research/blob/master/model.ipynb
- https://treeco.netlify.app

### OLS Regression:
- https://www.statsmodels.org/stable/examples/notebooks/generated/ols.html
OLS stands for Ordinary Least Squares, which is a method used to estimate the parameters of a linear regression model. In an OLS regression model, the goal is to find the line of best fit that minimizes the sum of the squared differences between the predicted values and the actual values of the dependent variable.

The OLS method works by calculating the slope and intercept of the line of best fit.

In [16]:
import pandas as pd
import pysal as ps
import statsmodels.api as sm
import geopandas as gpd
import libpysal as lp
from spreg import ML_Lag
from spreg import OLS
import numpy as np
from sklearn.metrics import mean_squared_error as mse

# Load the data 
#data = pd.read_csv('data_trees_modified.csv')
data = gpd.read_file('../data/geojson/geo_data_trees.geojson')

# take just the first 100 rows
data = data.iloc[:1000]
# remove the last row of the data (summary)
#data = data.drop([len(data)-1])

data['Total Annual Benefits (eur/yr)'] = data['Total Annual Benefits (eur/yr)'].astype(float)
#data['Carbon Storage (kg)'] = data['Carbon Storage (kg)'].astype(float)
data['DBH (cm)'] = data['DBH (cm)'].astype(float)
# create a new column with the index of the name of the tree (so all the trees with the same name will have the same index)
data['Name_id'] = data['Name'].astype('category').cat.codes

# Select the dependent variable and independent variables
y = data['Total Annual Benefits (eur/yr)'] # dependent
#X = data[['DBH (cm)', 'Name_id', 'Latitude', 'Longitude']] # independent
X = data[['Name_id']] # independent

# Create a spatial weights matrix
w = lp.weights.DistanceBand.from_dataframe(data, threshold=10, binary=True)

# Fit a spatial lag model
#model = sm.OLS(endog=y, exog=sm.add_constant(X), missing='drop')
#spatial_lag = ML_Lag(model.endog, model.exog, w=w, method='full', name_y=y.name, name_x=X.columns.tolist())
model = OLS(y.values.reshape(-1, 1), X.values, w=w, spat_diag=True)
print(model.summary)

# Print the regression results
#print(spatial_lag.summary)

REGRESSION
----------
SUMMARY OF OUTPUT: ORDINARY LEAST SQUARES
-----------------------------------------
Data set            :     unknown
Weights matrix      :     unknown
Dependent Variable  :     dep_var                Number of Observations:        1000
Mean dependent var  :      4.1657                Number of Variables   :           2
S.D. dependent var  :      3.6748                Degrees of Freedom    :         998
R-squared           :      0.0001
Adjusted R-squared  :     -0.0009
Sum squared residual:   13488.454                F-statistic           :      0.1376
Sigma-square        :      13.515                Prob(F-statistic)     :      0.7107
S.E. of regression  :       3.676                Log likelihood        :   -2719.856
Sigma-square ML     :      13.488                Akaike info criterion :    5443.711
S.E of regression ML:      3.6727                Schwarz criterion     :    5453.527

-----------------------------------------------------------------------------

In [ ]:
import geopandas as gpd
#import pysal
import libpysal as lp
from spreg import OLS
import numpy as np

# WE ARE WORKING WITH A SAMPLE OF THE DATA
# Load your tree dataset with coordinates and ecological benefits
trees = gpd.read_file('../data/geojson/geo_data_trees.geojson')
trees = trees.drop([len(trees)-1])

# Load environmental data
environment = gpd.read_file('../data/geojson/circoscrizioni.geojson')

# Create a spatial weights matrix
w = lp.weights.DistanceBand.from_dataframe(trees, threshold=100, binary=True)

# Convert the 'area' column to float (if needed)
environment['area'] = environment['area'].astype(float)

# { "type": "Feature", "properties": { "Tree ID": "129582", "Name": "Common pear", "DBH (cm)": "80.01", "Replacement Value (eur)": "8319.86", "Carbon Storage (kg)": "3253.572710773", "Carbon Storage (eur)": "522.74", "Gross Carbon Sequestration (kg/yr)": "1.678291769", "Gross Carbon Sequestration (eur/yr)": "0.27", "Avoided Runoff (l/yr)": "805.535248", "Avoided Runoff (eur/yr)": "1.53", "Carbon Avoided (kg/yr)": "0.0", "Carbon Avoided (eur/yr)": null, "Pollution Removal (g/yr)": "0.5386405", "Pollution Removal (eur/yr)": "1.51", "Energy Savings (eur/yr)": null, "Total Annual Benefits (eur/yr)": "3.31", "Height (m)": "3.00", "Oxygen Production (kg/yr)": "2.8", "Crown Height (m)": "1", "Crown Width (m)": "1.5", "Canopy Cover (m2)": "1.8", "Leaf Area (m2)": "3.5", "Leaf Biomass (kg)": "0.2", "Latitude": 44.497334971298301, "Longitude": 11.338233739967899, "Species Name": null }, "geometry": { "type": "Point", "coordinates": [ 11.338233739967899, 44.497334971298301 ] } },
# {"type": "Feature", "geometry": {"type": "Polygon", "coordinates": [[[11.296990350018913, 44.51662566856614], [11.297401407684434, 44.516516000814], ... , [11.296990350018913, 44.51662566856614]]]}, "properties": {"numero_cir": "9", "area": "11", "perimetro": "11", "nome": "TRIUMVIRATO-PIETRA", "fumetto": "Circoscrizione Borgo Panigale - Reno - Borgo Panigale"}},

# Create a spatial lag variable for the dependent variable
trees['Total Annual Benefits (eur/yr)'] = trees['Total Annual Benefits (eur/yr)'].str.replace(',', '.').astype(float)
y = trees['Total Annual Benefits (eur/yr)']
#ylag = pysal.lib.weights.lag_spatial(w, y)
#ylag = lp.weights.lag_spatial(w, y)

# Define the independent variable (e.g., 'area')
trees['Pollution Removal (eur/yr)'] = trees['Pollution Removal (eur/yr)'].str.replace(',', '.').astype(float)
X = trees[['Pollution Removal (eur/yr)']]

# arrays x and y not all of same length, cut to match on the basis of the shortest

# Perform spatial regression
#model = pysal.model.spreg.OLS(y.values.reshape(-1, 1), environment[['feature1', 'feature2']].values, w=w, name_y='Total Annual Benefits (eur/yr)', name_x=['feature1', 'feature2'], spat_diag=True)
#model = OLS(y.values.reshape(-1, 1), environment[['area', 'perimetro']].values, w=w, spat_diag=True)
model = OLS(y.values.reshape(-1, 1), X.values, w=w, spat_diag=True)
print(model.summary)


# Visualize the results, e.g., residuals, coefficients on a map
trees['residuals'] = model.u
trees['residuals'].describe()


Tutorial: 
- https://sustainability-gis.readthedocs.io/en/latest/lessons/L4/spatial_regression.html

In [2]:
from pysal.model import spreg
from pysal.lib import weights
from scipy import stats
import numpy as np
import pandas as pd
import geopandas as gpd
import seaborn as sns
import osmnx as ox
sns.set(style="whitegrid")

# Read OSM data - get administrative boundaries

# define the place query
query = {'city': 'Bologna'}

# get the boundaries of the place (add additional buffer around the query)
boundaries = ox.geocode_to_gdf(query, buffer_dist=5000)

# Let's check the boundaries on a map
boundaries.explore()

/var/folders/j8/fjrnp8w15sbf5q2fdgnpb0br0000gn/T/ipykernel_1974/518551908.py:17: UserWarning: The buffer_dist argument as been deprecated and will be removed in a future release. Buffer your results directly, if desired.
  boundaries = ox.geocode_to_gdf(query, buffer_dist=5000)
/Users/luca/opt/anaconda3/envs/geo_env/lib/python3.10/site-packages/mapclassify/classifiers.py:511: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  def _fisher_jenks_means(values, classes=5, sort=True):


In [25]:
import geopandas as gpd
#import pysal
import libpysal as lp
from spreg import OLS
import numpy as np

# WE ARE WORKING WITH A SAMPLE OF THE DATA
# Load your tree dataset with coordinates and ecological benefits
trees = gpd.read_file('../data/geojson/geo_data_trees.geojson')
# take a random sample of the dataset (1000 rows)
trees = trees.sample(n=5000)

#trees = trees.drop([len(trees)-1])

# Filter data geographically
trees_filtered = gpd.sjoin(trees, boundaries[["geometry"]])
trees_filtered = trees_filtered.reset_index(drop=True)

In [18]:
# change the total annual benefits to float
trees_filtered['Total Annual Benefits (eur/yr)'] = trees_filtered['Total Annual Benefits (eur/yr)'].str.replace(',', '.').astype(float)
# Here the tooltip parameter specifies which attributes are shown when hovering on top of the points
# The vmax parameter specifies the maximum value for the colormap (here, all 100 dollars and above are combined)
trees_filtered.explore(column="Total Annual Benefits (eur/yr)", cmap="Reds", scheme="quantiles", k=4, tooltip=["Species Name", "Total Annual Benefits (eur/yr)"], vmax=30, tiles="CartoDB Positron") 

# Baseline (nonspatial) regression

Before introducing explicitly spatial methods, we will run a simple linear regression model. This will allow us, on the one hand, set the main principles of hedonic modeling and how to interpret the coefficients, which is good because the spatial models will build on this; and, on the other hand, it will provide a baseline model that we can use to evaluate how meaningful the spatial extensions are.

In [28]:
# explanatory_vars = ['crown_height', 'crown_width', 'dbh', 'age', 'Leaf Area (m2)']

trees_filtered["Total Annual Benefits (eur/yr)"] = trees_filtered["Total Annual Benefits (eur/yr)"].astype(float)
#trees_filtered['Carbon Storage (kg)'] = trees_filtered['Carbon Storage (kg)'].astype(float)
trees_filtered['DBH (cm)'] = trees_filtered['DBH (cm)'].astype(float)
trees_filtered['Name_id'] = trees_filtered['Name'].astype('category').cat.codes
#explanatory_vars = ['DBH (cm)', 'Name_id', 'Latitude', 'Longitude']
explanatory_vars = ['DBH (cm)', 'Name_id']

In [38]:
trees_filtered["log_benefit"] = np.log(trees_filtered["Total Annual Benefits (eur/yr)"] + 0.000001)

In [30]:
# let us build a spatial weights matrix that connects every observation to its 8 nearest neighbors. 
# This will allow us to get extra diagnostics from the baseline model.

w = weights.KNN.from_dataframe(trees_filtered, k=8)
w.transform = 'R'
w

/Users/luca/opt/anaconda3/envs/geo_env/lib/python3.10/site-packages/libpysal/weights/weights.py:172: UserWarning: The weights matrix is not fully connected: 
 There are 9 disconnected components.
  warnings.warn(message)


In [31]:
m1 = spreg.OLS(trees_filtered[['log_benefit']].values, trees_filtered[explanatory_vars].values, 
                  name_y = 'log_benefit', name_x = explanatory_vars)

In [32]:
print(m1.summary)

REGRESSION
----------
SUMMARY OF OUTPUT: ORDINARY LEAST SQUARES
-----------------------------------------
Data set            :     unknown
Weights matrix      :        None
Dependent Variable  : log_benefit                Number of Observations:        5000
Mean dependent var  :      0.8134                Number of Variables   :           3
S.D. dependent var  :      1.1280                Degrees of Freedom    :        4997
R-squared           :      0.6689
Adjusted R-squared  :      0.6687
Sum squared residual:    2106.017                F-statistic           :   5047.0546
Sigma-square        :       0.421                Prob(F-statistic)     :           0
S.E. of regression  :       0.649                Log likelihood        :   -4933.094
Sigma-square ML     :       0.421                Akaike info criterion :    9872.187
S.E of regression ML:      0.6490                Schwarz criterion     :    9891.739

-----------------------------------------------------------------------------

# Spatially lagged exogenous regressors (WX)

In [39]:
trees_filtered["Height (m)"] = trees_filtered["Height (m)"].astype(float)

# Create weigts
w_height = weights.KNN.from_dataframe(trees_filtered, k=8)

# Assign spatial lag based on the pool values
lagged = trees_filtered.assign(w_height=weights.spatial_lag.lag_spatial(w_height, trees_filtered['Height (m)'].values))
lagged.head()

/Users/luca/opt/anaconda3/envs/geo_env/lib/python3.10/site-packages/libpysal/weights/weights.py:172: UserWarning: The weights matrix is not fully connected: 
 There are 9 disconnected components.
  warnings.warn(message)


Tree ID                Name  DBH (cm) Replacement Value (eur)  \
0   96390  European hackberry    39.878                 2464.81   
1   50356        European ash    39.878                 2403.11   
2    3436     Italian cypress    17.018                  675.98   
3   74371        Black locust    23.622                  848.11   
4   83081      Cottonwood spp    49.530                 2055.88   

  Carbon Storage (kg) Carbon Storage (eur) Gross Carbon Sequestration (kg/yr)  \
0        93.984339064                15.10                 3.0390688790000002   
1  434.58684969700005                69.82                 18.461209459000003   
2   98.38418505300001                15.81                        6.168856232   
3       142.700159602                22.93                 11.158372302000002   
4   660.7026461419999               106.15                 19.141598014000003   

  Gross Carbon Sequestration (eur/yr) Avoided Runoff (l/yr)  \
0                                0.49             882.00053   
1                                2.96           1019.789454   
2                                0.99    109.01980800000001   
3                                1.79            260.436208   
4                                3.08            579.924812   

  Avoided Runoff (eur/yr)  ... Leaf Area (m2)  Leaf Biomass (kg)   Latitude  \
0                    1.68  ...            3.5                0.2  44.500988   
1                    1.94  ...            3.5                0.2  44.504953   
2                    0.21  ...            3.5                0.2  44.480328   
3                    0.50  ...            3.5                0.2  44.507825   
4                    1.10  ...            3.5                0.2  44.513654   

   Longitude  Species Name                   geometry  index_right Name_id  \
0  11.366469          None  POINT (11.36647 44.50099)            0      53   
1  11.367985          None  POINT (11.36798 44.50495)            0      48   
2  11.352177          None  POINT (11.35218 44.48033)            0      74   
3  11.290505          None  POINT (11.29050 44.50783)            0      15   
4  11.390852          None  POINT (11.39085 44.51365)            0      35   

  log_benefit w_height  
0    1.340251     40.5  
1    1.918392     63.0  
2    0.336473     81.5  
3    1.018848    118.5  
4    1.662031     80.0  

[5 rows x 31 columns]

In [41]:
# Add pool to the explanatory variables
extended_vars = explanatory_vars + ["Height (m)", "w_height"]

m2 = spreg.OLS(lagged[['Total Annual Benefits (eur/yr)']].values, lagged[extended_vars].values, 
               name_y = 'Total Annual Benefits (eur/yr)', name_x = extended_vars)

In [42]:
print(m2.summary)

REGRESSION
----------
SUMMARY OF OUTPUT: ORDINARY LEAST SQUARES
-----------------------------------------
Data set            :     unknown
Weights matrix      :        None
Dependent Variable  :Total Annual Benefits (eur/yr)                Number of Observations:        5000
Mean dependent var  :      3.7113                Number of Variables   :           5
S.D. dependent var  :      3.2459                Degrees of Freedom    :        4995
R-squared           :      0.6944
Adjusted R-squared  :      0.6942
Sum squared residual:   16094.125                F-statistic           :   2837.8257
Sigma-square        :       3.222                Prob(F-statistic)     :           0
S.E. of regression  :       1.795                Log likelihood        :  -10017.234
Sigma-square ML     :       3.219                Akaike info criterion :   20044.467
S.E of regression ML:      1.7941                Schwarz criterion     :   20077.053

-----------------------------------------------------------

# Spatially lagged endogenous regressors (WY)

In [43]:
variables = explanatory_vars + ["Height (m)"]
m3 = spreg.GM_Lag(trees_filtered[['Total Annual Benefits (eur/yr)']].values, trees_filtered[variables].values, 
                  w=w,
                  name_y = 'ln(price)', name_x = variables)

In [44]:
print(m3.summary)

REGRESSION
----------
SUMMARY OF OUTPUT: SPATIAL TWO STAGE LEAST SQUARES
--------------------------------------------------
Data set            :     unknown
Weights matrix      :     unknown
Dependent Variable  :   ln(price)                Number of Observations:        5000
Mean dependent var  :      3.7113                Number of Variables   :           5
S.D. dependent var  :      3.2459                Degrees of Freedom    :        4995
Pseudo R-squared    :      0.6946
Spatial Pseudo R-squared:  0.6944

------------------------------------------------------------------------------------
            Variable     Coefficient       Std.Error     z-Statistic     Probability
------------------------------------------------------------------------------------
            CONSTANT      -1.0196800       0.0954363     -10.6843998       0.0000000
            DBH (cm)       0.0954490       0.0009760      97.7946087       0.0000000
             Name_id       0.0008845       0.0006018       

# Prediction performance of spatial models

In [45]:
mses = pd.Series({'OLS': mse(trees_filtered["Total Annual Benefits (eur/yr)"], m1.predy.flatten()), \
                  'OLS+W': mse(trees_filtered["Total Annual Benefits (eur/yr)"], m2.predy.flatten()), \
                  'Lag': mse(trees_filtered["Total Annual Benefits (eur/yr)"], m3.predy_e)
                    })
mses.sort_values()

OLS+W     3.218825
Lag       3.218896
OLS      14.975559
dtype: float64

### Ridge Regression:
Ridge regression is used when there is multicollinearity in the data, which means that the independent variables are highly correlated with each other. In this case, the OLS method may produce unstable and unreliable estimates of the coefficients. Ridge regression adds a penalty term to the sum of squared errors in the OLS method, which helps to reduce the variance of the estimates and improve the stability of the model.

In [ ]:
from sklearn.linear_model import Ridge
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split
import geopandas as gpd

# WE ARE WORKING WITH A SAMPLE OF THE DATA
# Load your tree dataset with coordinates and ecological benefits
trees = gpd.read_file('../data/geojson/geo_data_trees.geojson')
# take a random sample of the dataset (1000 rows)
trees = trees.sample(n=5000)

# Create a Ridge regression model
model = Ridge()